In [ ]:
%pip install kagglehub
import kagglehub

# path = kagglehub.dataset_download("aadyasingh55/fake-news-classification")

# print("Path to dataset files:", path)


[notice] A new release of pip is available: 24.2 -> 24.3.1
[notice] To update, run: pip install --upgrade pip
Note: you may need to restart the kernel to use updated packages.


/Library/Frameworks/Python.framework/Versions/3.12/lib/python3.12/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


100%|██████████| 39.0M/39.0M [00:05<00:00, 7.14MB/s]

Extracting files...


Path to dataset files: /Users/barnendupal/.cache/kagglehub/datasets/aadyasingh55/fake-news-classification/versions/1


In [2]:
import pandas as pd
import numpy as np
from sklearn.metrics import accuracy_score, classification_report, confusion_matrix
from sklearn.model_selection import train_test_split
from sklearn.pipeline import Pipeline
from sklearn.preprocessing import LabelEncoder


In [19]:
train_df = pd.read_csv('../Data/FakeNews/train.csv', on_bad_lines='skip', sep=';')
test_df = pd.read_csv('../Data/FakeNews/test.csv', on_bad_lines='skip', sep=';')
eval_df = pd.read_csv('../Data/FakeNews/evaluation.csv', on_bad_lines='skip', sep=';')

# Display basic information about each dataset
print("Train Dataset Info:")
print(train_df.info())
train_df.head()

print("\nEvaluation Dataset Info:")
print(eval_df.info())
eval_df.head()

print("\nTest Dataset Info:")
print(test_df.info())
test_df.head()

Train Dataset Info:
<class 'pandas.core.frame.DataFrame'>
RangeIndex: 24353 entries, 0 to 24352
Data columns (total 4 columns):
 #   Column      Non-Null Count  Dtype 
---  ------      --------------  ----- 
 0   Unnamed: 0  24353 non-null  int64 
 1   title       24353 non-null  object
 2   text        24353 non-null  object
 3   label       24353 non-null  int64 
dtypes: int64(2), object(2)
memory usage: 761.2+ KB
None

Evaluation Dataset Info:
<class 'pandas.core.frame.DataFrame'>
RangeIndex: 8117 entries, 0 to 8116
Data columns (total 4 columns):
 #   Column      Non-Null Count  Dtype 
---  ------      --------------  ----- 
 0   Unnamed: 0  8117 non-null   int64 
 1   title       8117 non-null   object
 2   text        8117 non-null   object
 3   label       8117 non-null   int64 
dtypes: int64(2), object(2)
memory usage: 253.8+ KB
None

Test Dataset Info:
<class 'pandas.core.frame.DataFrame'>
RangeIndex: 8117 entries, 0 to 8116
Data columns (total 4 columns):
 #   Column      Non

Unnamed: 0  ... label
0           0  ...     1
1           1  ...     1
2           2  ...     1
3           3  ...     1
4           4  ...     1

[5 rows x 4 columns]

In [20]:
train_df['content'] = train_df['title'] + train_df['text']
train_df.drop(['title','text'], axis = 1, inplace=True)
test_df['content'] = test_df['title'] + test_df['text']
test_df.drop(['title','text'], axis = 1, inplace=True)
eval_df['content'] = eval_df['title'] + eval_df['text']
eval_df.drop(['title','text'], axis = 1, inplace=True)
eval_df.head()

Unnamed: 0  label                                            content
0           0      1  Sanders back in U.S. Senate, blasts 'coloniali...
1           1      1  Kremlin: Syria peoples' congress being 'active...
2           2      0   Oregon Cop Convicted Of Shattering Biker’s Co...
3           3      0   Twitter Erupts With Glee Over #CruzSexScandal...
4           4      0  MUST WATCH VIDEO: Obama Tries To Trash Trump B...

In [21]:
%pip install gensim

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 24.0/24.0 MB 8.0 MB/s eta 0:00:00a 0:00:01
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 30.4/30.4 MB 7.9 MB/s eta 0:00:00a 0:00:01
  Attempting uninstall: scipy
    Found existing installation: scipy 1.14.1
    Uninstalling scipy-1.14.1:
      Successfully uninstalled scipy-1.14.1

[notice] A new release of pip is available: 24.2 -> 24.3.1
[notice] To update, run: pip install --upgrade pip
Note: you may need to restart the kernel to use updated packages.


In [26]:
from nltk.stem import WordNetLemmatizer
import re
from nltk.corpus import stopwords
import nltk
nltk.download('wordnet')

lemitizer = WordNetLemmatizer()

corpus = []

for i in range(0, len(train_df)):
    content = re.sub('[^a-zA-Z]', ' ', train_df['content'][i])
    content = content.lower()
    content = content.split()

    content = [lemitizer.lemmatize(word) for word in content if word not in stopwords.words('english')]
    content = ' '.join(content)
    corpus.append(content)


[nltk_data] Downloading package wordnet to
[nltk_data]     /Users/barnendupal/nltk_data...


In [27]:
corpus

['palestinian switch christmas light bethlehem anti trump protestramallah west bank reuters palestinian switched christmas light jesus traditional birthplace bethlehem wednesday night protest u president donald trump decision recognize jerusalem israel capital christmas tree adorned light outside bethlehem church nativity christian believe jesus born another ramallah next burial site former palestinian leader yasser arafat plunged darkness christmas tree switched order mayor today protest trump decision said fady ghattas bethlehem municipal medium officer said unclear whether illumination would turned main christmas festivity speech washington trump said decided recognize jerusalem israel capital move u embassy city israeli prime minister benjamin netanyahu said trump move marked beginning new approach israeli palestinian conflict said historic landmark arab muslim across middle east condemned u decision calling incendiary move volatile region european union united nation also voiced a

In [29]:
nltk.download('punkt')
from nltk import sent_tokenize
from gensim.utils import simple_preprocess

words = [] 
for sent in corpus:
    sent_token = sent_tokenize(sent)
    for token in sent_token:
        words.append(simple_preprocess(token))

words

[nltk_data] Downloading package punkt to
[nltk_data]     /Users/barnendupal/nltk_data...
[nltk_data]   Unzipping tokenizers/punkt.zip.


[['palestinian',
  'switch',
  'christmas',
  'light',
  'bethlehem',
  'anti',
  'trump',
  'protestramallah',
  'west',
  'bank',
  'reuters',
  'palestinian',
  'switched',
  'christmas',
  'light',
  'jesus',
  'traditional',
  'birthplace',
  'bethlehem',
  'wednesday',
  'night',
  'protest',
  'president',
  'donald',
  'trump',
  'decision',
  'recognize',
  'jerusalem',
  'israel',
  'capital',
  'christmas',
  'tree',
  'adorned',
  'light',
  'outside',
  'bethlehem',
  'church',
  'nativity',
  'christian',
  'believe',
  'jesus',
  'born',
  'another',
  'ramallah',
  'next',
  'burial',
  'site',
  'former',
  'palestinian',
  'leader',
  'yasser',
  'arafat',
  'plunged',
  'darkness',
  'christmas',
  'tree',
  'switched',
  'order',
  'mayor',
  'today',
  'protest',
  'trump',
  'decision',
  'said',
  'fady',
  'ghattas',
  'bethlehem',
  'municipal',
  'medium',
  'officer',
  'said',
  'unclear',
  'whether',
  'illumination',
  'would',
  'turned',
  'main',
  'ch

In [30]:
import gensim

model = gensim.models.Word2Vec(words)
model.corpus_count

24353

In [32]:
model.wv.similar_by_word('boy')

[('girl', 0.9009512662887573),
 ('teen', 0.7967702746391296),
 ('mom', 0.7601457238197327),
 ('kid', 0.755287766456604),
 ('teenage', 0.7545443177223206),
 ('teenager', 0.7376643419265747),
 ('girlfriend', 0.732504665851593),
 ('mother', 0.7181577682495117),
 ('sister', 0.7127874493598938),
 ('toddler', 0.7073655128479004)]

In [ ]:
def avgWord2Vec(doc):
    return np.mean([model.wv[word] for word in doc if word in model.wv.index_to_key])

X = []
for i in range(len(words)):
    X.append(avgWord2Vec(words[i]))


[0.026360609,
 0.045715794,
 -0.014818493,
 0.0334379,
 0.01517863,
 -0.011141899,
 -0.014688773,
 0.014192069,
 -0.027004208,
 -0.034175836,
 -0.0055343304,
 0.025361892,
 0.019221874,
 0.007528157,
 0.008434809,
 0.028459279,
 0.07019892,
 -0.038758464,
 -0.048595108,
 -0.014373204,
 0.004704221,
 0.033903453,
 -0.04386627,
 -0.014642633,
 -0.030469496,
 0.0024437204,
 -0.0024961063,
 -0.010441215,
 -0.0037461722,
 -0.04860788,
 0.03675674,
 0.010877427,
 0.028887011,
 -0.01805869,
 -0.005360807,
 -0.008899664,
 0.014674549,
 0.024954796,
 -0.042462133,
 -0.0019137238,
 0.05500188,
 0.017008774,
 0.030619744,
 -0.028745074,
 -0.010428751,
 0.0027656634,
 0.012276863,
 -0.011333277,
 0.0063601537,
 -0.013734961,
 -0.035064038,
 -0.01001696,
 0.037468437,
 -0.0029407428,
 0.0029853869,
 0.012656596,
 -0.0052417084,
 -0.01648273,
 -0.027563298,
 -0.034228876,
 -0.024810443,
 -0.02653456,
 0.0076698237,
 0.047643013,
 -0.025543574,
 0.012127676,
 0.015412089,
 0.006728792,
 -0.0689214,
 

In [41]:
y = train_df.iloc[:,1]
X = np.array(X)
y.shape,X.shape


((24353,), (24353,))

In [ ]:
df = pd.DataFrame()

for i in range(0, len(X)):
    new_row = pd.DataFrame(X[i].reshape(1, -1))
    df = pd.concat([df, new_row], ignore_index=True)

print(df.shape)

(24353, 1)
